In [1]:
import sys
import pickle
import gzip
import os,glob
import time
import numpy as np
import pandas as pd
import operator
import random
from  scipy import stats
#sys.path



import datetime
import math
import time
import itertools


from pymongo import MongoClient



import plotly.plotly as py
import plotly.graph_objs as go
from plotly import tools
import plotly.figure_factory as ff

import plotly
plotly.tools.set_credentials_file(username='juliettapc', api_key='nM6iUdx6dGaOiPXQTwpP')   # go to: https://plot.ly/settings/api#/   for a new key if needed

########## to be able to plot offline (without sending the plots to the plotly server every time)
import plotly.offline as offline
from plotly.graph_objs import *
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

init_notebook_mode(connected=True)
################



from IPython.core.display import display,HTML
display(HTML("<style>.container { width:100% !important; }</style>"))  # to make the notebook use the entire width of the browser


In [2]:

class MongoConnection(object):
    def __init__(self, cxnSettings, **kwargs):
        self.settings = cxnSettings
        self.mongoURI = self._constructURI()
        self.connect(**kwargs)
        self.ensure_index()

    def _constructURI(self):
        '''
        Construct the mongo URI
        '''
        mongoURI = 'mongodb://'
        #User/password handling
        if 'user'in self.settings and 'password' in self.settings:
            mongoURI += self.settings['user'] + ':' + self.settings['password']
            mongoURI += '@'
        elif 'user' in self.settings:
            print('Missing password for given user, proceeding without either')
        elif 'password' in self.settings:
            print('Missing user for given passord, proceeding without either')
        #Host and port
        try:
            mongoURI += self.settings['host'] + ':'
        except KeyError:
            print('Missing the hostname. Cannot connect without host')
            sys.exit()
        try:
            mongoURI += str(self.settings['port'])
        except KeyError:
            print('Missing the port. Substituting default port of 27017')
            mongoURI += str('27017')
        return mongoURI

    def connect(self, **kwargs):
        '''
        Establish the connection, database, and collection
        '''
        self.connection = MongoClient(self.mongoURI, **kwargs)
        #########
        try:
            self.db = self.connection[self.settings['db']]
        except KeyError:
            print("Must specify a database as a 'db' key in the settings file")
            sys.exit()
        #########
        try:
            self.collection = self.db[self.settings['collection']]
        except KeyError:
            print('Should have a collection.', end='')
            print('Starting a collection in database', end='')
            print(' for current connection as test.')
            self.collection = self.db['test']

    def tearDown(self):
        '''
        Closes the connection
        '''
        self.connection.close()

    def ensure_index(self):
        '''
        Ensures the connection has all given indexes.
        indexes: list of (`key`, `direction`) pairs.
            See docs.mongodb.org/manual/core/indexes/ for possible `direction`
            values.
        '''
        if 'indexes' in self.settings:
            for index in self.settings['indexes']:
                self.collection.ensure_index(index[0], **index[1])



#############################

merged_papers_settings = {
    "host": "chicago.chem-eng.northwestern.edu",
    "port": "27017",
    "db": "web_of_science_aux",
    "collection": "merged_papers",
    "user": "mongoreader",
    "password": "emptycoffeecup"
}

papers_con = MongoConnection(merged_papers_settings)




#############################

dais_settings = {
    "host": "chicago.chem-eng.northwestern.edu",
    "port": "27017",
    "db": "web_of_science_aux",
    "collection": "ut_dais_all",
    "user": "mongoreader",
    "password": "emptycoffeecup"
}

dais_con = MongoConnection(dais_settings)



In [3]:

%time df_merged = pickle.load(open('../data/df_reference_cite_plos_no_self-cit_one_ref_per_sect_ONLY_ARTICLES_early_cit.pkl', 'rb'))


#### dictionary category-code
#   ../data/dict_categ_code.pkl



dict_categ_code = pickle.load(open('../data/dict_categ_code.pkl', 'rb'))
#print (len(dict_categ_code))



print ("from the entire df ",df_merged.shape, "  ; and plos one records:",  df_merged[df_merged['plos_j1']== "PLOS ONE"].shape,"\n\n")
# {'Biology and life sciences': 0,
#  'Computer and information sciences': 1,
#  'Earth sciences': 2,
#  'Ecology and environmental sciences': 3,
#  'Engineering and technology': 4,
#  'Medicine and health sciences': 5,
#  'People and places': 6,
#  'Physical sciences': 7,
#  'Research and analysis methods': 8,
#  'Science policy': 9,
#  'Social sciences': 10}

dict_code_categ={}
dict_size_categ={}
for categ in dict_categ_code:
    code = str(dict_categ_code[categ])
    
    df_selection_categ = df_merged[df_merged['categ_codes'].str.contains(code)]
   # print (categ, code, df_selection_categ.shape)
    size= len(df_selection_categ)
    dict_size_categ[size] = categ
    dict_code_categ[code] = categ

for size in reversed(sorted(dict_size_categ)):
    print (size, dict_size_categ[size])
df_merged.head()

CPU times: user 4.39 s, sys: 2.77 s, total: 7.17 s
Wall time: 25.7 s
from the entire df  (5787634, 30)   ; and plos one records: (5368044, 30) 


5087022 Biology and life sciences
3807430 Medicine and health sciences
3260173 Research and analysis methods
1766358 Physical sciences
1035009 Computer and information sciences
647228 Social sciences
579580 People and places
526791 Ecology and environmental sciences
444753 Earth sciences
322656 Engineering and technology
36492 Science policy


occurence     reference_UT  reference_rank  regex_sect_index  cite_count  \
0          1  A1995QY75100004               1                 0        60.0   
1          2  A1995QY75100004               1                 3        60.0   
4          1  000263911400006               3                 0         5.0   
5          1  000289279600018               4                 0        29.0   
6          3  000289279600018               4                 3        29.0   

   ref_pub_year  paper_cite_count  plos_pub_year  sect_char_pos  \
0        1995.0                 2         2013.0            139   
1        1995.0                 2         2013.0            494   
4        2009.0                 2         2013.0            142   
5        2011.0                 2         2013.0            269   
6        2011.0                 2         2013.0           3844   

   sect_char_total           ...            total_refs categ_codes  \
0             4029           ...                    37         0 5   
1             5398           ...                    37         0 5   
4             4029           ...                    37         0 5   
5             4029           ...                    37         0 5   
6             5398           ...                    37         0 5   

  self_citation  number_authors  plos_article_type  num_cit_young_ref_by2009  \
0             0               5          @ Article                       NaN   
1             0               5          @ Article                       NaN   
4             0               5          @ Article                       0.0   
5             0               5          @ Article                       0.0   
6             0               5          @ Article                       0.0   

   num_cit_young_ref_by2010 num_cit_young_ref_by2011  \
0                       NaN                      NaN   
1                       NaN                      NaN   
4                       0.0                      NaN   
5                       0.0                      0.0   
6                       0.0                      0.0   

   num_cit_young_ref_by2012 num_cit_young_ref_by2013  
0                       NaN                      NaN  
1                       NaN                      NaN  
4                       NaN                      NaN  
5                       3.0                      NaN  
6                       3.0                      NaN  

[5 rows x 30 columns]

In [4]:

def select_data_for_plotting(df_merged, v1_string, years, string_filtering_x, string_references_age, string_isolated_ref, string_self_ref, string_code_categ, string_journal, string_plos_field):
    """
    This function selects a subset of the total dataset acording to a set of parameters.

            

    Parameters
    ----------
    df_merged : pandas dataframe
        Original dataframe to select from
        
    v1_string : str
        Main variable 
        
    years : list of int
        List of selected years
        
    string_filtering_x : str
        Variable for heatmap plot
        
    string_references_age : str
        Selected 'young' or 'old' or 'all' references for the analysis
        
    string_isolated_ref : str
        Selected isolated (1) or group (0) or 'all' references for the analysis
        
    string_self_ref : str
         Selected self references (1) or not self references (0) or 'all' references for the analysis
         
    string_code_categ : str
        Selected PLos category: from 0 to 10 or multiple ones
        
    string_journal : int
        Selected PLoS journal
        
    string_plos_field : str
        Selected PLoS field


    Returns
    -------
    dataframe
        Selected subset of rows from the original dataset (all columns).

    """

    
    
    
    
    
    
    print ("original size:",df_merged.shape)



    ##### preselection by plos publication year
    print (years)
    preselection_df = df_merged[df_merged['plos_pub_year'].isin(years)]  
    print ("size of preselection1 (by plos years):",preselection_df.shape)





    #### i remove self-citations
    if (string_self_ref==0) or  ( string_self_ref == 1 ): 
        preselection_df = preselection_df[preselection_df['self_citation']== string_self_ref ]  
        if string_self_ref ==0:
            string_self_ref = ", no self-cit"
        elif string_self_ref ==1:
            string_self_ref = ", only self-cit"





    ######### preselection by isolated or group references:
    if (string_isolated_ref==0) or  ( string_isolated_ref == 1 ): 
        preselection_df0 = preselection_df[preselection_df['isolated_citation']== string_isolated_ref ]  

        if string_isolated_ref ==0:
            string_isolated_ref = ", group ref"
        elif string_isolated_ref ==1:
            string_isolated_ref = ", isolated ref"
    else:    
        preselection_df0 = preselection_df   
        print ("size of preselection1 (by isolated/group ref):",preselection_df0.shape, string_isolated_ref)








    ######### preselection by plos ONE subject category:
    if string_code_categ=="": 
        preselection_df111 = preselection_df0
    else:    
        if " " not in string_code_categ:  # to include one single category
            preselection_df111 = preselection_df0[preselection_df0['categ_codes'].str.contains(string_code_categ)]        
            string_code_categ = " "+dict_code_categ[string_code_categ]  

        else:  # if multiple codes-categories
            list_codes = string_code_categ.split(" ")
            print (list_codes)

            if len(list_codes) >= 2:              
                preselection_df111 = preselection_df0[ preselection_df0['categ_codes'].str.contains('|'.join(list_codes)) ]  # to look for partial matches from a list of strings!!!!!


            string_code_categ = "" 
            for code in list_codes:
                string_code_categ += "-"+dict_code_categ[code] 


        print (" size of preselection (by plos ONE subject category):",preselection_df111.shape, string_code_categ)








    ######### preselection by plos journal:
    if string_journal=="": 
        preselection_df1 = preselection_df111
    else:    
        preselection_df1 = preselection_df111[preselection_df111['plos_j1']== string_journal ]  
    print (" size of preselection2 (by plos journal):",preselection_df1.shape, string_journal)







    ######### preselection by plos field:
    if string_plos_field=="": 
        preselection_df2 = preselection_df1
    else:    
        preselection_df2 = preselection_df1[preselection_df1['plos_field']== string_plos_field ]  
    print (" size of preselection2 (by plos field):",preselection_df2.shape, string_plos_field)


    preselection_df3 = preselection_df2

    if v1_string ==  'cite_count'  or       v1_string ==  'log_num_cit_ref'   or v1_string == 'log2_num_cit_ref':

        string_age_selv1_stringection=''

        ##### preselection only young/old references:        
        if string_references_age == "young":
            time_window = 1
            string_age_selection="only young references from >="+ str((min(years)-time_window))
            preselection_df3 = preselection_df2[preselection_df2['ref_pub_year'] >= (min(years)-time_window) ]   
            print ("  size of preselection3 (only young references):",preselection_df3.shape, string_age_selection)

        elif string_references_age == "old":
            time_window = 10
            string_age_selection="only old references from <="+str((min(years)-time_window))
            preselection_df3 = preselection_df2[preselection_df2['ref_pub_year'] <= (min(years)-time_window) ]   
            print ("  size of preselection3 (only young references):",preselection_df3.shape,string_age_selection )

        else:
            string_age_selection="young&old"       
            print ("  No preselection by age of references:",preselection_df3.shape )




  

    
    
    
    
    
    
    return preselection_df3

In [5]:
#### i set the parameters to do the selection of the subset of plos papers that I want    
    
    
v1_string =  'cite_count'

years= [2009,2010]  #[2005,2006,2007,2008,2009,2010,2011,2012,2013,2014,2015,2016,2017]   #### SELECT THE PLOS YEARS TO BE INCLUDED

string_filtering_x = 'paper_cite_count'   

string_references_age = ""     # AGE OF REFERENCES TO BE INCLUDED:  'young'     'old'   or   "" for including all

string_isolated_ref = ""   # WHETHER OR NOT TO INCLUDE ISOLATED REFERENCES:   # 0  or 1 (or empty string, to include all ref)

string_self_ref =0    #  WHETHER OR NOT TO INCLUDE SELF-REFERENCES:  #     0  or 1 (or empty string, to include all ref)




#  SELECT HERE THE PLOS FIELD:
string_code_categ="0" #  plos ONE categories:  the codes are strings (0  TO 10), not integers. if i want to include multiple subjects:  "1 2 8"


#  '0': 'Biology and life sciences'             6,032,537 --
#  '1': 'Computer and information sciences'     1,207,799 --
#  '2': 'Earth sciences'                        533,155 --
#  '3': 'Ecology and environmental sciences'    624,142 --
#  '4': 'Engineering and technology'            382,247 --
#  '5': 'Medicine and health sciences'          4,535,926  -- 
#  '6': 'People and places'                     691,523 --
#  '7': 'Physical sciences'                     2,100,827 --
#  '8': 'Research and analysis methods'         3,871,470 --
#  '9': 'Science policy'                        43,360 --
#  '10': 'Social sciences'                      755,899 --

# GIVE IT A MATCHING FIELD NAME TAG FOR THE OUTPUT FILES:
field_name = 'biol'
    
    
    
    
    
    
    

string_journal=""   #  plos journals 
string_plos_field=""  #  WoS subject categories. 




preselection_df3 = select_data_for_plotting(df_merged, v1_string, years, string_filtering_x, string_references_age, string_isolated_ref, string_self_ref, string_code_categ, string_journal, string_plos_field)




print ("\nTot # records included:",len(preselection_df3),"   # number of plos papers:",len(preselection_df3.paper_UT.unique()), "   # unique ref:", len(preselection_df3.reference_UT.unique()),'\n')

####################################


## 2010:     Tot # records included: 256358    # number of plos papers: 6617    # unique ref: 177852 
# 2009-2010: Tot # records included: 416901    # number of plos papers: 10955    # unique ref: 267265 


original size: (5787634, 30)
[2009, 2010]
size of preselection1 (by plos years): (440231, 30)
size of preselection1 (by isolated/group ref): (440231, 30) 
 size of preselection (by plos ONE subject category): (416901, 30)  Biology and life sciences
 size of preselection2 (by plos journal): (416901, 30) 
 size of preselection2 (by plos field): (416901, 30) 
  No preselection by age of references: (416901, 30)

Tot # records included: 416901    # number of plos papers: 10955    # unique ref: 267265 



In [ ]:
### i query the mongoDB to get the abstract of the list of references' UT from the selected papers:

list_UT_ref = preselection_df3.reference_UT.unique()

dict_ref_UT_abstract = {}
dict_ref_UT_title = {}

print (len(list_UT_ref))

cont_abst = 0
cont_no_abst = 0

cont_title = 0
cont_no_title = 0


cont = 0
for ref_UT in list_UT_ref:
    
    item = papers_con.collection.find_one({"UT" : ref_UT}, {'AB':1,'TI':1})  # the output of a find_one cursor is a DICTIONARY!!!   citations:   cites received by the paper (currently updated value!)
     
    dict_ref_UT_abstract[ref_UT] = np.nan

    print (cont)
    cont  +=1
    try:
        
        #print (ref_UT, item['AB'])
        
        abstract = item['AB']

        dict_ref_UT_abstract[ref_UT] = abstract
        cont_abst +=1

    except: 
        #print (ref_UT, item['issue']['PY'])#,item['issue']['AB'])#pass
        cont_no_abst +=1
        
        
        
        
        
    try:
        
        #print (ref_UT, item['AB'])
        
        title = item['TI']

        dict_ref_UT_title[ref_UT] = title
        cont_title +=1

    except: 
        #print (ref_UT, item['issue']['PY'])#,item['issue']['TI'])#pass
        cont_no_title +=1
        
        
        
        
      

print (cont_abst/float(len(dict_ref_UT_abstract)),  cont_no_abst/float(len(dict_ref_UT_abstract)))
print (cont_title/float(len(dict_ref_UT_title)),  cont_no_title/float(len(dict_ref_UT_title)))






print ("done.", len(dict_ref_UT_abstract),"dumping dict ref-abstracts 2009-2010 "+field_name+".......")         
with open('../data/dict_ref_UT_abstract'+str(2009)+"_"+str(2010)+field_name+'.pkl', 'wb') as handle:
         pickle.dump(dict_ref_UT_abstract, handle, protocol = 2)
print ("written:",'../data/dict_ref_UT_abstract'+str(2009)+"_"+str(2010)+field_name+'.pkl')   









print ("done.", len(dict_ref_UT_title),"dumping dict ref-title 2010 "+field_name+".......")         
with open('../data/dict_ref_UT_title'+str(2009)+"_"+str(2010)+field_name+'.pkl', 'wb') as handle:
         pickle.dump(dict_ref_UT_title, handle, protocol = 2)
print ("written:",'../data/dict_ref_UT_title'+str(2009)+"_"+str(2010)+field_name+'.pkl')   




############################################################3

### i build dataframes from the dictionaries ref_UT:title and ref_UT:abstract

df_abstracts_ref_FIELD_2010 = pd.DataFrame(list(dict_ref_UT_abstract.items()), columns=['reference_UT', 'Abstract'])
#df_abstracts_ref_FIELD_2010 = pickle.load(open('../data/dict_ref_UT_title'+str(2010)+field_name+'.pkl', 'rb'))


df_title_ref_FIELD_2010 = pd.DataFrame(list(dict_ref_UT_title.items()), columns=['reference_UT', 'Title'])





       


df_new = pd.merge(df_title_ref_FIELD_2010, df_abstracts_ref_FIELD_2010, on='reference_UT', how='left')

### i only want references from 1995-2000
df_selection_1995_2000 = preselection_df3[(preselection_df3['ref_pub_year'] >= 1995 ) & (preselection_df3['ref_pub_year'] <= 2000 )]  

list_ref_UT_1995_2000 =  df_selection_1995_2000.reference_UT.unique()


print (len(list_ref_UT_1995_2000))



selection_new_df = df_new[df_new['reference_UT'].isin(list_ref_UT_1995_2000)]  




with open('../data/df_abstracts_titles_ref_2009_2010'+field_name+'.pkl', 'wb') as handle:
            pickle.dump(selection_new_df, handle, protocol = 2)       
print ("written:",'../data/df_abstracts_titles_ref_2009_2010'+field_name+'.pkl',len(selection_new_df))   






    

In [ ]:
#lista_paper_UT_comput = preselection_df3.paper_UT.unique()  PAPERS

len(lista_paper_UT_comput)   # comput: 1253   # bio: 6617   # physical: 2111   social: 744

In [ ]:
#lista_paper_UT_biol = preselection_df3.paper_UT.unique()

len(lista_paper_UT_biol)

In [ ]:
#lista_paper_UT_physical = preselection_df3.paper_UT.unique()

len(lista_paper_UT_physical)

In [ ]:
#lista_paper_UT_social = preselection_df3.paper_UT.unique()

len(lista_paper_UT_social)

In [ ]:
len(list_ref_biol)

In [12]:
#####  i combine the reference records from two different fields for benchmarking:




df_comput = pickle.load(open('../data/df_abstracts_titles_ref_2010comput.pkl', 'rb'))   #  5612
df_comput = df_comput.sort_values(by=['reference_UT']).reset_index(drop=True)
list_ref_comput = df_comput.reference_UT.unique()




df_social = pickle.load(open('../data/df_abstracts_titles_ref_2010social.pkl', 'rb'))   #  3474
df_social = df_social.sort_values(by=['reference_UT']).reset_index(drop=True)
list_ref_social = df_social.reference_UT.unique()


df_physical = pickle.load(open('../data/df_abstracts_titles_ref_2010physical.pkl', 'rb'))   # 11197
df_physical = df_physical.sort_values(by=['reference_UT']).reset_index(drop=True)
list_ref_physical = df_physical.reference_UT.unique()



df_biol = pickle.load(open('../data/df_abstracts_titles_ref_2010biol.pkl', 'rb'))   #  32347
df_biol = df_biol.sort_values(by=['reference_UT']).reset_index(drop=True)
list_ref_biol = df_biol.reference_UT.unique()


In [ ]:


df_biol = pickle.load(open('../data/df_abstracts_titles_ref_2010biol.pkl', 'rb'))
df_biol = df_biol.sort_values(by=['reference_UT']).reset_index(drop=True)
list_ref_biol = df_biol.reference_UT.unique()


In [10]:

%time df_testing = pickle.load(open('../data/df_abstracts_titles_ref_2010comput.pkl', 'rb'))
df_testing

CPU times: user 16.9 ms, sys: 2.1 ms, total: 19 ms
Wall time: 71.9 ms


reference_UT                                              Title  \
1      000075667500002  Clinical manifestations and prognostic feature...   
30     000081021000007  Expression of long-term potentiation of the st...   
35     000085520900029  Disposition of methamphetamine and its metabol...   
39     000081584300052  Expression mechanisms underlying NMDA receptor...   
42     A1995QP88900008  D1/D5 RECEPTOR AGONISTS INDUCE A PROTEIN SYNTH...   
44     A1996VY43300008  D1/D5 dopamine receptor activation increases t...   
47     000075335800002  Disruption of dopamine D-1 receptor gene expre...   
51     A1995TF26400022  SEROTONIN REDUCES INHIBITION VIA 5-HT1A RECEPT...   
54     000080942500008  Calcium- and activity-dependent synaptic plast...   
55     000088903600044  Intracellular calcium dependence of transmitte...   
62     A1996TW14300002  Psychostimulants depress excitatory synaptic t...   
69     000073531200014  Effect of the selective 5-HT1A receptor antago...   
73     A1995RJ36400013  PHARMACOKINETIC AND PHARMACODYNAMIC ANALYSIS O...   
74     000083757300039  Spontaneous locomotor activity and pharmacokin...   
96     000085252800016  The causes and consequences of genetic variati...   
126    A1995QP88900049  CHLOROPLAST GENE SEQUENCE DATA SUGGEST A SINGL...   
131    000083913600053  Angiosperm phylogeny inferred from multiple ge...   
137    000165228200045  The evolutionary fate and consequences of dupl...   
144    A1997WV34000013  A phylogeny of the chloroplast gene rbcL in th...   
146    000078716000002  Nodulation response of woody Papilionoid speci...   
148    000081001100004  Development of N-2-fixing nodules on the wetla...   
149    000087051200005  Temporal and spatial order of events during th...   
151    000082946400010              CAP3: A DNA sequence assembly program   
153    A1997XU79300002  Gapped BLAST and PSI-BLAST: a new generation o...   
160    A1997YB06200010  Retrograde community structure in the late Eoc...   
182    000086454300035  Nonrandom extinction and the loss of evolution...   
195    000076616600052  Neural learning rules for the vestibulo-ocular...   
196    A1996VY43300040  Behavioral analysis of signals that guide lear...   
203    000078872200003  Cerebellar learning in the vestibulo-ocular re...   
206    000077606800025  Synaptic modifications in cultured hippocampal...   
...                ...                                                ...   
32575  A1997YE73800010  Inhibition of FIV replication by a ribozyme th...   
32585  A1995QH63800002  LASER CYTOMETRIC ANALYSIS OF FIV-INDUCED INJUR...   
32586  000074730200071  CXCR4 is required by a nonprimate lentivirus: ...   
32588  A1995QB47600005  FELINE IMMUNODEFICIENCY VIRUS - AN INTERESTING...   
32589  A1996VF33000007  Genetic diversity of Argentine isolates of fel...   
32590  A1995QD24800004  PHYLOGENETIC ANALYSIS OF THE LONG TERMINAL REP...   
32591  A1997WZ57100008  Genetic diversity of feline immunodeficiency v...   
32594  A1997XL12600013  Phylogenetic analysis of feline immunodeficien...   
32595  A1995QX93100045  NUCLEOTIDE-SEQUENCE OF FELINE IMMUNODEFICIENCY...   
32596  A1997XT71000015  Analysis of the genetic diversity and phylogen...   
32603  A1996UF24700038  Molecularly cloned feline immunodeficiency vir...   
32605  A1995RU78400026  INDUCTION OF ACCELERATED FELINE IMMUNODEFICIEN...   
32608  A1997XV26600002  Prosody in the comprehension of spoken languag...   
32615  A1995QQ45500009  TIME, CHANGE, AND MOTION - THE EFFECTS OF STIM...   
32616  000081301100004  Auditory accounts of temporal factors in the p...   
32625  A1995TJ63600009  POSTTRAUMATIC-STRESS-DISORDER IN THE NATIONAL ...   
32630  000086152200001  A cognitive model of posttraumatic stress diso...   
32633  000089818100048  Replaying the game: Hypnagogic images in norma...   
32654  A1997YD42100006  Physical activity and its association with oth...   
32660  A1996WB11900006  The role of lifestyle in health: The epidemiol...   
32662 

In [11]:
len(df_testing.reference_UT.unique())

5612

In [ ]:
df_ref_clusters.shape

In [7]:
##### Martin ran an algorithm to get the clusters on papers and on words (topics) and gave me this output file:


#%time df_ref_clusters = pd.read_csv('../data/doc-clustering_df_abstracts_titles_ref_biol_2010_nmin10_removestopTrue_stemmingTrue_nrun10.csv')  # 2009 bio papers, ref from 1995-2000

%time df_ref_clusters = pd.read_csv('../data/doc-clustering_df_abstracts_titles_ref_2009_2010biol_nmin10_removestopTrue_stemmingTrue_nrun10.csv') # 2009-2010 bio papers, ref from 1995-2000

df_ref_clusters

CPU times: user 30.1 ms, sys: 7.35 ms, total: 37.5 ms
Wall time: 148 ms


Unnamed: 0               UT     0    1    2   3  4
0               0  000089825700038     0    0    0   0  0
1               1  000072361600007     1    1    1   0  0
2               2  000165228200045     2    2    1   0  0
3               3  000071878500068     3    3    2   2  0
4               4  000083638400006     3    3    2   2  0
5               5  000077748100013     4  246    2   2  0
6               6  A1995QR07000025     5    5    3   3  0
7               7  000165076100003     6    6    4   4  1
8               8  A1996UL97400016     7    7    5   5  0
9               9  000074950000037     8    8    6   6  0
10             10  000168366100026     8    8    6   6  0
11             11  000073113200016     8    8    6   6  0
12             12  000084602200014     9    9    7   7  0
13             13  000071616000046    10    8    6   6  0
14             14  A1995RD45200023    11   10    8   8  1
15             15  000085770300004    11   10    8   8  1
16             16  000088707500012    11   10    8   8  1
17             17  A1995TL17800001    12   10    8   8  1
18             18  A1996UF45900005    11   10    8   8  1
19             19  000081095400010    11   10    8   8  1
20             20  000087021100027    11   10    8   8  1
21             21  A1997YJ81700006    13   11    8   8  1
22             22  000078313300008    14   12    9   1  1
23             23  000085399200036    15   13   10   9  1
24             24  000085902800067    16   14   11   7  0
25             25  000082805400036    17   15   12   7  0
26             26  A1995TD44000006    17   15   12   7  0
27             27  000076060100023    18   15   12   7  0
28             28  000079538800014    19   15   12   7  0
29             29  000083685100004    20   16   13   7  0
...           ...              ...   ...  ...  ...  .. ..
48272       48272  000086155800008  1771  391   25   4  1
48273       48273  A1997WN61800006  1416  330   10   9  1
48274       48274  000087362200007   612  310  105   2  0
48275       48275  000072681900003   351   33   28  12  0
48276       48276  000082012800096    10    8    6   6  0
48277       48277  A1995QU29500013  1335  292   69  14  0
48278       48278  A1997XZ08400002  2202  255   46   6  0
48279       48279  000071228800002  2202  255   46   6  0
48280       48280  A1997XU08700007  2202  255   46   6  0
48281       48281  A1995RM51900020    32   26   21  12  0
48282       48282  A1997WZ28400008    32   26   21  12  0
48283       48283  000080441600003   621   45    9   1  1
48284       48284  A1997XG14200002  2233  346   13   7  0
48285       48285  000081218600017  1681  301   61  16  1
48286       48286  000072350300006   564   14   11   7  0
48287       48287  000072350300007   478  116   11   7  0
48288       48288  000071898600006   133   98   61  16  1
48289       48289  000079976200012   564   14   11   7  0
48290       48290  000074064000011  1763  282   11   7  0
48291       48291  A1997WF65200003   479   45    9   1  1
48292       48292  A1996UQ21300008   277   45    9   1  1
48293       48293  000076035400013  1860   11    8   8  1
48294       48294  A1995RJ70700006  1096   11    8   8  1
48295       48295  A1995RF04000004  1520  299   61  16  1
48296       48296  A1995RA88900011  2038  299   61  16  1
48297       48297  000088608000090  2038  299   61  16  1
48298       48298  000085657200005  2038  299   61  16  1
48299       48299  A1997XZ45500006  1743   98   61  16  1
48300       48300  A1997YJ24400002   476  111   61  16  1
48301       48301  A1995QL21100003  2038  299   61  16  1

[48302 rows x 7 columns]

In [8]:
def fix_ref_UT(row):
    
    ref_UT = row.UT
    string_UT=str(ref_UT)
    if len (string_UT) <15:
        actual_lenght = len(string_UT)
       
        if actual_lenght == 14:
            return '0'+str(ref_UT)
        elif actual_lenght == 13:
            return '00'+str(ref_UT)
        elif actual_lenght == 12:
            return '000'+str(ref_UT)
        elif actual_lenght == 11:
            return '0000'+str(ref_UT)
        elif actual_lenght == 10:
            return '00000'+str(ref_UT)
        
    else:
        return ref_UT

    
df_ref_clusters['new_ref_UT'] = df_ref_clusters.apply (lambda row: fix_ref_UT(row),axis=1)
df_ref_clusters.drop(['UT'], axis=1, inplace=True)
df_ref_clusters.rename(columns={'new_ref_UT': 'reference_UT'}, inplace=True)
df_ref_clusters

Unnamed: 0     0    1    2   3  4     reference_UT
0               0     0    0    0   0  0  000089825700038
1               1     1    1    1   0  0  000072361600007
2               2     2    2    1   0  0  000165228200045
3               3     3    3    2   2  0  000071878500068
4               4     3    3    2   2  0  000083638400006
5               5     4  246    2   2  0  000077748100013
6               6     5    5    3   3  0  A1995QR07000025
7               7     6    6    4   4  1  000165076100003
8               8     7    7    5   5  0  A1996UL97400016
9               9     8    8    6   6  0  000074950000037
10             10     8    8    6   6  0  000168366100026
11             11     8    8    6   6  0  000073113200016
12             12     9    9    7   7  0  000084602200014
13             13    10    8    6   6  0  000071616000046
14             14    11   10    8   8  1  A1995RD45200023
15             15    11   10    8   8  1  000085770300004
16             16    11   10    8   8  1  000088707500012
17             17    12   10    8   8  1  A1995TL17800001
18             18    11   10    8   8  1  A1996UF45900005
19             19    11   10    8   8  1  000081095400010
20             20    11   10    8   8  1  000087021100027
21             21    13   11    8   8  1  A1997YJ81700006
22             22    14   12    9   1  1  000078313300008
23             23    15   13   10   9  1  000085399200036
24             24    16   14   11   7  0  000085902800067
25             25    17   15   12   7  0  000082805400036
26             26    17   15   12   7  0  A1995TD44000006
27             27    18   15   12   7  0  000076060100023
28             28    19   15   12   7  0  000079538800014
29             29    20   16   13   7  0  000083685100004
...           ...   ...  ...  ...  .. ..              ...
48272       48272  1771  391   25   4  1  000086155800008
48273       48273  1416  330   10   9  1  A1997WN61800006
48274       48274   612  310  105   2  0  000087362200007
48275       48275   351   33   28  12  0  000072681900003
48276       48276    10    8    6   6  0  000082012800096
48277       48277  1335  292   69  14  0  A1995QU29500013
48278       48278  2202  255   46   6  0  A1997XZ08400002
48279       48279  2202  255   46   6  0  000071228800002
48280       48280  2202  255   46   6  0  A1997XU08700007
48281       48281    32   26   21  12  0  A1995RM51900020
48282       48282    32   26   21  12  0  A1997WZ28400008
48283       48283   621   45    9   1  1  000080441600003
48284       48284  2233  346   13   7  0  A1997XG14200002
48285       48285  1681  301   61  16  1  000081218600017
48286       48286   564   14   11   7  0  000072350300006
48287       48287   478  116   11   7  0  000072350300007
48288       48288   133   98   61  16  1  000071898600006
48289       48289   564   14   11   7  0  000079976200012
48290       48290  1763  282   11   7  0  000074064000011
48291       48291   479   45    9   1  1  A1997WF65200003
48292       48292   277   45    9   1  1  A1996UQ21300008
48293       48293  1860   11    8   8  1  000076035400013
48294       48294  1096   11    8   8  1  A1995RJ70700006
48295       48295  1520  299   61  16  1  A1995RF04000004
48296       48296  2038  299   61  16  1  A1995RA88900011
48297       48297  2038  299   61  16  1  000088608000090
48298       48298  2038  299   61  16  1  000085657200005
48299       48299  1743   98   61  16  1  A1997XZ45500006
48300       48300   476  111   61  16  1  A1997YJ24400002
48301       48301  2038  299   61  16  1  A1995QL21100003

[48302 rows x 7 columns]

In [9]:
df_ref_clusters.shape
preselection_df3.shape



df_selection_bio_95_00 = preselection_df3[ (preselection_df3['ref_pub_year'] >= 1995) & (preselection_df3['ref_pub_year'] <= 2000)]  
df_selection_bio_95_00.shape

(77414, 30)

In [10]:
# lista_ref_2010_tot = preselection_df3.reference_UT.unique()
# lista_ref_select_abstr = df_ref_clusters.reference_UT.unique()

lista_ref_select_abstr = df_selection_bio_95_00.reference_UT.unique()

len(lista_ref_select_abstr)

51023

In [17]:
df_new = pd.merge(df_selection_bio_95_00, df_ref_clusters, on='reference_UT', how='left')

df_new.rename(columns={'4': 'cluster_indx_top'}, inplace=True)  #  4 is the higher (coarser) structure level from the clustering results  (ojo!! for the results of only 2009, it is 3)
df_new.rename(columns={'3': 'cluster_indx_2nd'}, inplace=True) 
df_new 

occurence     reference_UT  reference_rank  regex_sect_index  \
0              1  000089825700038               1                 0   
1              1  000072361600007              16                 2   
2              1  000165228200045              21                 3   
3              1  000071878500068               2                 0   
4              1  000083638400006              12                 0   
5              2  000083638400006              12                 2   
6              1  000077748100013              36                 2   
7              1  A1995QR07000025              45                 2   
8              1  000165076100003              46                 3   
9              1  A1996UL97400016               1                 0   
10             2  A1996UL97400016               1                 2   
11             1  000074950000037               6                 0   
12             2  000074950000037               6                 2   
13             1  000168366100026               8                 0   
14             1  000073113200016              11                 0   
15             1  000084602200014              15                 0   
16             1  000071616000046              38                 3   
17             1  A1995RD45200023              12                 0   
18             2  A1995RD45200023              12                 3   
19             1  000085770300004              16                 3   
20             1  000088707500012              20                 0   
21             1  A1995TL17800001              21                 0   
22             1  A1996UF45900005              36                 3   
23             1  000081095400010              38                 3   
24             1  000087021100027              40                 3   
25             1  A1997YJ81700006              43                 3   
26             2  A1997YJ81700006              43                 1   
27             1  000078313300008              27                 1   
28             1  000085399200036              29                 3   
29             1  000083961300007               2                 0   
...          ...              ...             ...               ...   
77384          5  A1997XG14200002               2                 3   
77385          1  000081218600017               5                 0   
77386          3  000081218600017               5                 3   
77387          1  000072350300006              11                 0   
77388          2  000072350300006              11                 3   
77389          1  000072350300007              19                 0   
77390          1  000071898600006              30                 2   
77391          1  000079976200012              39                 3   
77392          1  000084581800029              55                 1   
77393          1  000074064000011              56                 1   
77394          1  A1997WF65200003               3                 0   
77395          1  A1996UQ21300008               6                 0   
77396          1  000074405900008               7                 0   
77397          1  A1997YA42300007              13                 0   
77398          1  A1997XD86900055              17                 0   
77399          1  000165228200045              19                 0   
77400          1  000165831300031               6                 0   
77401          2  000165831300031               6                 3   
77402          1  000076035400013              37                 3   
77403          1  A1995RJ70700006              38                 3   
77404          1  A1996WF04200003              39                 3   
77405          1  000075664500008              42                 3   
77406          1  A1995RF04000004               9                 3   
77407          1  A1995RA88900011              10                 0   
77408          1  0000886080000

In [ ]:
#df_new.cluster_indx.unique()
lista_listas = []

In [ ]:
for i in range(len(lista_listas)):
    for j in range(len(lista_listas)):
        if j>=i:
            print (i, j, stats.ks_2samp(lista_listas[i], lista_listas[j]))
            print (i, j, stats.mannwhitneyu(lista_listas[i], lista_listas[j]))
            print ()
    print ()
    print ()

In [ ]:
cont = 0 
preselection_df3 = df_new
print ("all:",cluster_flag, preselection_df3.shape, "  <avg # cit ref>:",preselection_df3.cite_count.median(), " min:",preselection_df3.cite_count.min(), " max:",preselection_df3.cite_count.max())

for  cluster_flag in range(11):   #= 11   #'all'  # 'all'  0 1 2 3 4 ... 10  (USE INTEGERS!)
#cluster_flag = 9  #'all'  # 'all'  0 1 2 3 4 ... 10  (USE INTEGERS!)
    
    preselection_df3 = df_new[df_new['cluster_indx']== cluster_flag ]  
    cont += len(preselection_df3)

    print ("cluster:",cluster_flag, preselection_df3.shape, "  <avg # cit ref>:",preselection_df3.cite_count.median(), " min:",preselection_df3.cite_count.min(), " max:",preselection_df3.cite_count.max())

print (cont)

In [106]:
### code from Figure 3A and Figure 3B



#for  cluster_flag in range(2):   #= 11   #'all'  # 'all'  0 1 2 3 4 ... 10  (USE INTEGERS!)

cluster_level = 'top'  # top or 2nd

cluster_flag = 1  #'all'  # 'all'  0 1 2 3 4 ... 10  (USE INTEGERS!)


v1_string =  'cite_count' 


dict_group_subset_data={}
dict_group_quantiles_size={}



if cluster_flag == 'all':
    preselection_df3 = df_new

else:
    if cluster_level == '2nd':
        preselection_df3 = df_new[df_new['cluster_indx_2nd']== cluster_flag ]  
    elif cluster_level == 'top':
        preselection_df3 = df_new[df_new['cluster_indx_top']== cluster_flag ]  



print ("cluster:",cluster_flag, preselection_df3.shape, "  <avg # cit ref>:",preselection_df3.cite_count.median(), " min:",preselection_df3.cite_count.min(), " max:",preselection_df3.cite_count.max())


N_plos=len(preselection_df3.paper_UT.unique())        ## this values are overall, for the title   
N_all=len(preselection_df3)



fig_font_colors=''

fig_colorscale = "Reds"





top_space = 150
if v1_string ==  'cite_count'  :
    colorbar_string = 'Citations'
    if string_references_age == "old" :
        colorbar_string = ''
else:
    colorbar_string = 'Age [yr]'
    top_space = 100
    text_abc = '(b)'





#### i get the bins number of citation of the plos papers OJO!!!!! i want the same bins for all papers (so i calculate them before separating into sections but after all the preselections)


list_q=[0.3,0.6,.9,.99,1]    # for the percentile sections for number of citations of the PLOS papers

#quantiles=sorted(list(df_plos[string_filtering_x].quantile(list_q).to_dict().items())) #mean 10.68 
quantiles=sorted(list(preselection_df3[string_filtering_x].quantile(list_q).to_dict().items())) #mean 10.68 


lista_bins_plos_citations=[]
old_value=0
for item in quantiles:
    try:
        pair=[old_value, int(item[1])]    
    except:  # if it is a nan:
        pair=[old_value, item[1]]

    lista_bins_plos_citations.append(pair)

    try:
        old_value = int(item[1])
    except:
        old_value = item[1]

# print (lista_bins_plos_citations)



### i modify the bins to separete the zero-one
# lista_bins_plos_citations[0][0]=2       
# lista_bins_plos_citations = [[0,2]] + lista_bins_plos_citations    
#print (lista_bins_plos_citations)

################################################









lista_titulos_sets = []



lista_sections = ["Introduction","Methods","Results","Discussion"]

cont=0
for item in lista_bins_plos_citations:

    minimo = item[0]
    maximo = item[1]


    preselection_df4 = preselection_df3[(preselection_df3[string_filtering_x] >= minimo)  &  (preselection_df3[string_filtering_x] < maximo)]
    #print ("size of preselection3 (by cit bin plos):",df_select.shape, item)



    x1_All = list(preselection_df4[v1_string])









    for string_section in lista_sections:


        ##### preselection to include only occurences in a section of the paper
        if  string_section == "Introduction":
            section=0
        elif  string_section == "Methods":
            section=1
        elif  string_section == "Results":
            section=2
        elif  string_section == "Discussion":
            section=3





        df_select = preselection_df4[preselection_df4['regex_sect_index']== section]   
        #print ("size of preselection2 (by section):",preselection_df3.shape, string_section)

        x1 = list(df_select[v1_string])       





        if cont ==0:            
            #group=string_section+" Bottom "+str(int(100.*list_q[0]))+"%"  
            group=string_section+" Bottom" 
        elif cont ==1:            
            #group=string_section+" "+str(int(100.*list_q[0]+1))+"%-"+str(int(100.*list_q[-4]))+"%"         
            group=string_section+" Typical"       
        elif cont==2:
             #group=string_section+" "+str(int(100.*list_q[1]+1))+"%-"+str(int(100.*list_q[-3]))+"%"     
             group=string_section+" Good"    
        elif cont==3: 
            #group=string_section+" "+str(int(100.*list_q[2]+1))+"%-"+str(int(100.*list_q[-2]))+"%"    
            group=string_section+" High"
        elif cont==4:
            #group=string_section+" Top "+str(int(100.-100.*list_q[-2]))+"%"    
            group=string_section+" Top"


        lista_titulos_sets.append(group)    





        ######### i get also quantiles for each cell:    
        list_quantiles_cell=[.25,.5,.75]

        values_quantiles=list(df_select[v1_string].quantile(list_quantiles_cell))#sorted(list(df_select[v1_string].quantile(list_quantiles_cell).to_dict().items()))      

        tupla=values_quantiles + [len(x1)]

        dict_group_quantiles_size[group] = tupla

        dict_group_subset_data[group]=x1



    cont +=1





################ i also add the median values for the section across all data in the preselection
for string_section in lista_sections:


    if  string_section == "Introduction":
        section=0
    elif  string_section == "Methods":
        section=1
    elif  string_section == "Results":
        section=2
    elif  string_section == "Discussion":
        section=3


    df_select = preselection_df3[preselection_df3['regex_sect_index']== section]   

    list_quantiles_cell=[.25,.5,.75]
    values_quantiles=list(df_select[v1_string].quantile(list_quantiles_cell))#sorted(list(df_select[v1_string].quantile(list_quantiles_cell).to_dict().items()))      
    tupla=values_quantiles + [len(df_select)]



#     dict_group_quantiles_size[string_section+" ALL PLOS"]=tupla
#     dict_group_subset_data[string_section+" ALL PLOS"]=x1_All    







########  I create the x, y, z lists of values for the heatmap

lista_y=lista_sections
#lista_x=[" Bottom 30%"," 31% to 60%"," 61% to 90%" ," 91% to 99%"," Top 1%"," ALL"]
#lista_bin_names=[" ALL PLOS"," Bottom "+str(int(100.*list_q[0]))+"%"," "+str(int(100.*list_q[0]+1))+"% to "+str(int(100.*list_q[-4]))+"%",\
              #   " "+str(int(100.*list_q[1]+1))+"% to "+str(int(100.*list_q[-3]))+"%" ," "+str(int(100.*list_q[2]+1))+"% to "+str(int(100.*list_q[-2]))+"%"," Top "+str(int(100.-100.*list_q[-2]))+"%"]


lista_bin_names=[" Bottom"," Typical"," Good"," High"," Top"]






#lista_x=[" Bottom 30%"," 31% to 60%"," 61% to 90%" ," 91% to 99%"," Top 1%"]   

lista_x=lista_bin_names

lista_z25=[]
lista_z50=[]
lista_z75=[]
lista_z_sizes=[]

for x_value in lista_x:    
    aux_lista25=[]
    aux_lista50=[]
    aux_lista75=[]
    aux_lista_sizes=[]

    for y_value in lista_y:       

        llave=y_value+x_value

        try:
            value=int(dict_group_quantiles_size[llave][0])
        except:  # if it is a nan:
            value=dict_group_quantiles_size[llave][0]
        aux_lista25.append(value)




        try:
            value=int(dict_group_quantiles_size[llave][1])
        except:  # if it is a nan:
            value=dict_group_quantiles_size[llave][1]
        aux_lista50.append(value)




        try:
            value=int(dict_group_quantiles_size[llave][2])
        except:  # if it is a nan:
            value=dict_group_quantiles_size[llave][2]
        aux_lista75.append(value)




        value_size=dict_group_quantiles_size[llave][3]
        aux_lista_sizes.append(value_size)


        #print (y_value," ",x_value, value, value_size)
    lista_z25.append(aux_lista25)
    lista_z50.append(aux_lista50)
    lista_z75.append(aux_lista75)




    lista_z_sizes.append(aux_lista_sizes)



# print ("lista values 25%-quantile:",lista_z25)
# print ("lista sizes",lista_z_sizes)





lista_text_z=[]
for i in range(len(lista_z_sizes)):
    aux=[]
    for j in range(len(lista_z_sizes[0])):
        #value=str(lista_z25[i][j])+"-<b>"+str(lista_z50[i][j])+"</b>-"+str(lista_z75[i][j])+"<br>("+str(lista_z_sizes[i][j])+")"            #"Median:"+str(lista_z[i][j])+"<br> N:"+str(lista_z_sizes[i][j])
        value=str(lista_z25[i][j])+"-<b>"+str(lista_z50[i][j])+"</b>-"+str(lista_z75[i][j])+"<br>("+str(format(lista_z_sizes[i][j], ',d'))+")"            #"Median:"+str(lista_z[i][j])+"<br> N:"+str(lista_z_sizes[i][j])



        aux.append(value)
    lista_text_z.append(aux)
# print (lista_text_z)

fig_colorscale




fig_filename = '../plots/heatmap_hot_topics_'+cluster_level+'_level_cluster'+str(cluster_flag)



path=   '/home/staff/julia/at_Northwestern/In_Text_Citations/In-Text-Citations-New/plots/'



fig = ff.create_annotated_heatmap(z=lista_z50, x=lista_sections, y=lista_bin_names, annotation_text=lista_text_z, colorscale=fig_colorscale, font_colors=fig_font_colors,showscale=True, colorbar=dict(title=colorbar_string, titleside='right' ),)#, reversescale=True)



#fig = ff.create_annotated_heatmap(z=lista_z50, x=lista_sections, y=lista_bin_names,  colorscale=fig_colorscale, font_colors=fig_font_colors,showscale=True)#, reversescale=True)
fig.layout.title = ""# fig_title_plot

fig['layout']['xaxis']['side'] = 'bottom'
fig.layout.xaxis.update({'title': 'Section'})


fig.layout.yaxis.update({'title': 'Impact Group'})



font_gral=25  # 20 if i wanna see it on the browser, 40 if i care about the png output
fig['layout']['font']['size'] = font_gral


# if v1_string ==  'cite_count'  :
#     if string_references_age == "young":  
#         #fig.layout.update({'title': '$d, r \\text{ (solar radius)}$'})
#         fig['layout']['title'] = "Young references"
#     elif string_references_age == "old":  
#         fig.layout.update({'title': 'Old references'})

#     fig.layout.update({'font': dict(size=25)})

# fig.layout.yaxis.update({'title': 'Citation percentile of plos paper'})




font_gral=45  # 20 if i wanna see it on the browser, 40 if i care about the png output
fig['layout']['font']['size'] = font_gral


# Altering x axis
#fig['layout']['xaxis']['tickfont']['family'] = 'Gill Sans MT'
fig['layout']['xaxis']['tickangle'] = 0
fig['layout']['yaxis']['tickangle'] = -90
fig['layout']['xaxis']['titlefont']['size'] = font_gral + 20
fig['layout']['yaxis']['titlefont']['size'] = font_gral

fig['layout']['xaxis']['tickfont']['size'] = font_gral -7 
fig['layout']['yaxis']['tickfont']['size'] = font_gral -15




fig['layout']['margin']=dict(
        l=200,
       # r=50,
        b=150,
        t=top_space,
        pad=15
    )





#  annotations=[
#         dict(
#             x=-.05,
#             y=1.05,
#             xref='paper',
#             yref='paper',
#             text=text_abc,
#             showarrow=False,
#             font=dict(               
#                 size=80,  
#                 color='black'
#             ),

#         )
#     ],


offline.plot(fig, auto_open=True, image = 'png', image_filename=fig_filename ,image_width=2000, image_height=1200, filename=fig_filename+'.html', validate=True)





# old, age >=15 years; Tot # records included: 88209    # number of plos papers: 12895    # unique ref: 61867 
# young, age <=2 years;  Tot # records included: 104113    # number of plos papers: 13442    # unique ref: 66644 












###########################################
######################################################3
########################################################


##############  I RUN THE TESTS FOR THE COMPARISON OF ALL PAIRS OF SUB-SETS:  (all pair-wise comparison cells in figure 2b, and 3a, 2b)

#####  mann-whitney U   test



lista_indeces = [[1,1],[1,2],[1,3],[1,4],\
                 [2,1],[2,2],[2,3],[2,4],\
                 [3,1],[3,2],[3,3],[3,4],\
                 [4,1],[4,2],[4,3],[4,4],\
                 [5,1],[5,2],[5,3],[5,4]]

#fig_colorscale=  [ [0., '#f2f2f2'], [threshold_zero,'#cce6ff'], [0.9999, '#0059b3'], [1.,'#bdbdbd']]# '#ffffff']]  0: white,  .99999: blue,  1: grey
fig_colorscale=  [ [0., '#0059b3'], [.5,'#c7dcf1'], [1.,'#bdbdbd']] #  0 or anything significant: blue,   .5 or anithing NON signif: light-blue,     1: grey






lista_bin_names = ["Bottom","Typical","Good","High","Top"]
lista_sections  =  ['Intro', 'Methods', 'Results', 'Discussion']






tot_rows = 5
tot_cols = 4  

test = "MW"  # KS to test if the distributions are different or  MW for testing just whether the medians are different 




list_keys_macro = ['Introduction Top',    'Methods Top',    'Results Top',   'Discussion Top', \
                   'Introduction High',   'Methods High',  'Results High',  'Discussion High', \
                   'Introduction Good',   'Methods Good',   'Results Good',  'Discussion Good', \
                   'Introduction Typical', 'Methods Typical', 'Results Typical', 'Discussion Typical', \
                   'Introduction Bottom',  'Methods Bottom',  'Results Bottom', 'Discussion Bottom']


list_keys_heatmap = ['Introduction Bottom', 'Methods Bottom',  'Results Bottom', 'Discussion Bottom',\
                     'Introduction Typical', 'Methods Typical', 'Results Typical', 'Discussion Typical',\
                     'Introduction Good',   'Methods Good',   'Results Good',  'Discussion Good', \
                     'Introduction High',   'Methods High',  'Results High',  'Discussion High', \
                     'Introduction Top',   'Methods Top',    'Results Top',   'Discussion Top'  ]


### i apply the bonferroni correction:  new p-_value_threshold  required for significance = old_p_value /Number of comparisons = 0.001 / (20*19/2)     

threshold_zero = 0.0001 / (float(len(list_keys_macro))*float(len(list_keys_macro)-1)/2.)    # to round up to zero the very small p_values



# lista_titulos_sets  (from the previous cell)

# ['Introduction Bottom',
#  'Methods Bottom',
#  'Results Bottom',
#  'Discussion Bottom',
#  'Introduction Typical',
#  'Methods Typical',
#  'Results Typical',
#  'Discussion Typical',
#  'Introduction Good',
#  'Methods Good',
#  'Results Good',
#  'Discussion Good',
#  'Introduction High',
#  'Methods High',
#  'Results High',
#  'Discussion High',
#  'Introduction Top',
#  'Methods Top',
#  'Results Top',
#  'Discussion Top']






lista_tot_datos=[]

total_cont =0
for i in list_keys_macro:
    lista_listas=[]
    aux_lista=[]
    cont=1

    for j in list_keys_heatmap:

        set1 = dict_group_subset_data[i]
        set2 = dict_group_subset_data[j]

        if test == "KS":
            p_value = stats.ks_2samp(set1, set2)[1] 
        elif test == "MW":
            p_value = stats.mannwhitneyu(set1, set2,  alternative='two-sided')[1]  


        if p_value <= threshold_zero:  #i round up to zero the very small p_values
                p_value =0.

        else:
            p_value = .5  ### I ONLY CARFE ABOUT WHETGER IT IS SIGNIFICANT OR NOT, I DONT CARE ABOUT THE EXACT P-VALUE ONCE IT IS NOT SIGNIFICANT

        if i == j:  # i single out manually the self comparison
            p_value=1.001  



        aux_lista.append(p_value)

        cont +=1

        if cont > tot_cols:
            lista_listas.append(aux_lista)                  
            aux_lista=[]
            cont=1



    total_cont +=1
    lista_tot_datos.append(lista_listas)





##############################

### I create an empty plot
fig_macro = None
fig_macro = tools.make_subplots(rows=tot_rows, cols=tot_cols, shared_xaxes=True, shared_yaxes=True, vertical_spacing = 0.01, horizontal_spacing = 0.01,   )


for i in range(len(lista_tot_datos)):
    datos = lista_tot_datos[i]

    cont_rows = lista_indeces[i][0]
    cont_cols = lista_indeces[i][1]

    trace1 = go.Heatmap(z=datos,
                       x=lista_sections,
                       y=lista_bin_names,                        
                       colorscale = fig_colorscale,
                       showscale=False,)
                        #reversescale=True, )#    )






    # i add each plot
    fig_macro.append_trace(trace1, cont_rows, cont_cols)






fontsize=32 
fig_macro['layout']['font'].update({'size': fontsize})






# fig_macro['layout']['margin'].update({'l': 250})   # i add extra space to the margins of the plots
# fig_macro['layout']['margin'].update({'b': 150})  
# fig_macro['layout']['margin'].update({'t': 50})   



lista_bin_names = ["Bottom","Typical","Good","High","Top"]
lista_sections  =  ['Introduction', 'Methods', 'Results', 'Discussion']



# i use the axis title of the small plots as values of the axis of the macro plot
fig_macro['layout']['xaxis1'].update(title=lista_sections[0])  
fig_macro['layout']['xaxis2'].update(title=lista_sections[1])
fig_macro['layout']['xaxis3'].update(title=lista_sections[2])
fig_macro['layout']['xaxis4'].update(title=lista_sections[3])


fig_macro['layout']['yaxis1'].update(title=lista_bin_names[4])   # ojo con el orden aqui!!
fig_macro['layout']['yaxis2'].update(title=lista_bin_names[3])
fig_macro['layout']['yaxis3'].update(title=lista_bin_names[2])
fig_macro['layout']['yaxis4'].update(title=lista_bin_names[1])
fig_macro['layout']['yaxis5'].update(title=lista_bin_names[0])







#  annotations=[
#         dict(
#             x=-.05,
#             y=1.05,
#             xref='paper',
#             yref='paper',
#             text='(b)',
#             showarrow=False,
#             font=dict(               
#                 size=80,  
#                 color='black'
#             ),

#         )
#     ],






image_filename = '../plots/multiple_comparisons_heatmap_hot_topics_'+cluster_level+'_level_cluster'+str(cluster_flag)

# offline.plot(fig_macro, auto_open=True, image = 'png', image_filename=image_filename ,image_width=3000, image_height=2200,
#               filename=image_filename, validate=True)













###### ALL: 
#cluster: all (77414, 36)   <avg # cit ref>: 145.0  min: 0.0  max: 40223.0

###### TOP LEVEL:
# cluster: 1 (23483, 36)   <avg # cit ref>: 132.0  min: 1.0  max: 22839.0
#cluster: 0 (49720, 36)   <avg # cit ref>: 149.0  min: 0.0  max: 40223.0


########  SECOND LEVEL:
#cluster: 0 (5738, 36)   <avg # cit ref>: 252.0  min: 1.0  max: 40223.0
#cluster: 1 (6600, 36)   <avg # cit ref>: 124.0  min: 1.0  max: 22839.0

cluster: 1 (23483, 36)   <avg # cit ref>: 132.0  min: 1.0  max: 22839.0
This is the format of your plot grid:
[ (1,1) x1,y1 ]  [ (1,2) x2,y1 ]  [ (1,3) x3,y1 ]  [ (1,4) x4,y1 ]
[ (2,1) x1,y2 ]  [ (2,2) x2,y2 ]  [ (2,3) x3,y2 ]  [ (2,4) x4,y2 ]
[ (3,1) x1,y3 ]  [ (3,2) x2,y3 ]  [ (3,3) x3,y3 ]  [ (3,4) x4,y3 ]
[ (4,1) x1,y4 ]  [ (4,2) x2,y4 ]  [ (4,3) x3,y4 ]  [ (4,4) x4,y4 ]
[ (5,1) x1,y5 ]  [ (5,2) x2,y5 ]  [ (5,3) x3,y5 ]  [ (5,4) x4,y5 ]



In [43]:
#### run old Figure 4b cell first to get the list of values!!!!


data = []
   
for cluster_flag in range(2):
   
        dict_group_subset_data={}
        dict_group_quantiles_size={}



        #preselection_df3 = df_new[df_new['cluster_indx_2nd']== cluster_flag ]  
        preselection_df3 = df_new[df_new['cluster_indx_top']== cluster_flag ]  


        aux = preselection_df3['cite_count']
        a = aux.tolist()




        #list_colors = ['#67a9cf','#91cf60','#f1a340','#d7191c']



      

        ### equivalent to normalized cumulative distribution  !!!
        x = np.sort(a)
        y = np.linspace(0, 1, len(a), endpoint=False)


        trace0 = go.Scatter(
            x = x,
            y = y,
            mode = 'lines',
           # name = list_annot_x[i],
            marker = dict(         
                  #  color = c,
                    line = dict(
                            width = 50,
                          #  color = c
                    )
                )
        )

        data.append(trace0)







layout = Layout(    
    showlegend = False,

    xaxis=dict(
        title= "Number of citations received",   
#         titlefont=dict(
#             #size=font_axes,
#             color='black'),  
#         tickfont=dict(   
#             #family=font,
#             size=font_ticks,
#             color='black'),
         #range = [1, 500],#range=[np.log10(0.1),np.log10(max_x)],   # because the axis is log, the range needs to be in log units too!  :(
         type='log',            
        ),

    yaxis=dict(
        title='Probability density',
        #type='log',
#         titlefont=dict(            
#             size=font_axes,
#             color='black'
#         #    color='lightgrey'
#         ),  
#         tickfont=dict(   
#             #family=font,
#             size=font_ticks,
#             color='black'
#         ),
        ),                



)       


fig = dict(data=data, layout=layout)

fig['layout']['xaxis']['title'] = "Number of citations"
fig['layout']['yaxis']['title'] = "Cumulative probability density"
#fig['layout']['title'] = string_top_bottom_plos.capitalize()+" 10% papers"    




font_gral=50   # 20 if i wanna see it on the browser, 40 if i care about the png output
fig['layout']['font']['size'] = font_gral
fig['layout']['xaxis']['titlefont']['size'] = font_gral +10
fig['layout']['yaxis']['titlefont']['size'] = font_gral +10

fig['layout']['legend']=dict( x=0.75, y=.9,  ) #font=dict(size=20) 





fig['layout']['margin']=dict(
        l=250,
        r=50,
        b=150,
        t=150,  
    )    














offline.plot(fig)

'file:///home/staff/julia/at_Northwestern/In_Text_Citations/In-Text-Citations-New/notebooks/temp-plot.html'

In [12]:
# ######   Histogram number of citations of references in different clusters/topics


# lista_listas = []

# v1_string = 'cite_count'

# x1 = df_new[v1_string]



# font=20
# font_ticks=50
# font_axes=60


# data = []

# trace1= Histogram(
#         x=x1, 
#      marker=dict(
#         color='#848484',
#     ),
#        # name='high cit',
#        histnorm='probability',
#        name="All ref (95-00) from plos bio papers 2010",
#     cumulative=dict(enabled=True)
# )

# lista_listas.append(x1)

# data.append(trace1)  






# # list_sect = ["Introduction","Methods","Results","Discussion"]
# # list_colors = ["#7171C6","#4EEE94","#FF4040","#FFA500"]


# for cluster in range(11):
    
#     df_selection=df_new[ (df_new['cluster_indx'] == cluster)]   
#     print (cluster, df_selection.shape)
#     x1 = df_selection[v1_string]
#     lista_listas.append(x1)

    
#     trace= Histogram(
#             x=x1, 
# #          marker=dict(
# #             color=list_colors[index],
# #         ),           
#            histnorm='probability',
#            name=str(cluster),
#         cumulative=dict(enabled=True)
#         )


#     data.append(trace)  





# layout = Layout(    

#     bargap=0.2,

#     xaxis=dict(
#         title= 'Number of citations' , #v1_string.replace("_"," "),   
#         #range=[-.49, 3.49],
#         titlefont=dict(            
#             size=font_axes,
#             color='black'
#         #    color='lightgrey'
#         ),  
#         tickfont=dict(              
#             size=font_ticks,
#             color='black'
#         ),
#         #type='log'
#         #tickvals=[0,1,2,3],
#         #ticktext=["Introduction","Methods","Results","Discussion"]
#     ),
#     yaxis=dict(
#         title='PDF',
#         type='log',
#         titlefont=dict(
#             size=font_axes,
#             color='black'
#         #    color='lightgrey'
#         ),  
#         tickfont=dict(               
#             size=font_ticks,
#             color='black'
#         ),
#     ),                

#     margin=go.Margin(
#         l=200,
#        # r=50,
#         b=150,
#         #t=100,
#        # pad=4
#     ),



# #     bargroupgap=0.1
# )       



# fig = Figure(data=data, layout=layout)

# iplot(fig, filename='Number_citations_by_ref_topic_clusters.html')


# offline.plot(fig, auto_open=True, image = 'png', image_filename="Age_references_by_section.html",
#              output_type='file', image_width=2000, image_height=1400, filename='/home/staff/julia/at_Northwestern/In_Text_Citations/In-Text-Citations-New/plots/Number_citations_by_ref_topic_clusters.html', validate=False)





# ### add data for all, for the KS test
# x1 = df_new[v1_string]
# lista_listas.append(x1)

0 (49720, 36)
1 (23483, 36)
2 (0, 36)
3 (0, 36)
4 (0, 36)
5 (0, 36)
6 (0, 36)
7 (0, 36)
8 (0, 36)
9 (0, 36)
10 (0, 36)


/home/staff/julia/.pyenv/versions/3.6.4/envs/psy/lib/python3.6/site-packages/plotly/graph_objs/_deprecations.py:396: DeprecationWarning:

plotly.graph_objs.Margin is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.layout.Margin




In [ ]:
# ###  MORE TEXT IN EACH CELL AND FLIPPING COLUMNS-ROWS IN THE HEATMAP ...........
# #  annotated heatmap plot for median publication year (OR CITATIONS) of the references used in the different sections, and separating by citation category of the plos
# ### NEWWWW  :  removed bottom row 

# ## FIGURE 2B  AND FIGURE 3A AND FIGURE 3B


# dict_group_subset_data={}
# dict_group_quantiles_size={}

# ######### in this cell I SELECT the data i want to plot (by multiple criteria), as well as the variable that will encode with color:
# ######### ######### ######### ######### ######### ######### ######### 


# v1_string = 'cite_count'   #      cite_count    diff_year_plos_ref 
       
  
# string_references_age = "all"   #"#old"  # young # all   for the selection of what references i include
  
  
  
# top_space = 150
# if v1_string ==  'cite_count'  :
#     colorbar_string = 'Citations'
#     if string_references_age == "old" :
#         colorbar_string = ''
# else:
#     colorbar_string = 'Age [yr]'
#     top_space = 100
#     text_abc = '(b)'

# years=[2010] 



# #years=[2005,2006,2007,2008,2009,2010,2011,2012,2013,2014,2015,2016,2017] 



# list_q=[0.3,0.6,.9,.99,1]    # for the percentile sections for number of citations of the PLOS papers
 
    
# string_filtering_x = 'paper_cite_count'   # bins by plos' citations on the x-axis ###      
  
    
      
      
    
    
    
    

# string_isolated_ref = ""   #""   #"  #""   # 0  or 1 (or empty string, to include all ref)
# #list_strings = [1,0]
# #for  string_isolated_ref  in list_strings:
    
    


# string_self_ref =0         #""      # ""   #1   # 0  or 1 (or empty string, to include all ref)   OJO!!! THIS NEW FILE DOES NOT INCLUDE SELF-CITATIONS TO BEGING WITH




# ######### plos ONE categories. 
# string_code_categ="" #  ojo!!! the codes are strings, not integers. if i want to include multiple subjects:  "1 2 8"


# #list_strings=['0', '1', '4', '5', '7', '8', '2 3','10 6 9']
# #for string_code_categ in list_strings:


# #   Biology and Live Sciences;   Computational Sciences;   Engineering;   Medicine;   Physical Sciences;   Research and Analysis; \
# #  Earth Sciences and Ecology;   Social Sciences, Political Sciences and People & Places



# #  '0': 'Biology and life sciences'             6,032,537 --
# #  '1': 'Computer and information sciences'     1,207,799 --
# #  '10': 'Social sciences'                      755,899 --
# #  '2': 'Earth sciences'                        533,155 --
# #  '3': 'Ecology and environmental sciences'    624,142 --
# #  '4': 'Engineering and technology'            382,247 --
# #  '5': 'Medicine and health sciences'          4,535,926  -- 
# #  '6': 'People and places'                     691,523 --
# #  '7': 'Physical sciences'                     2,100,827 --
# #  '8': 'Research and analysis methods'         3,871,470 --
# #  '9': 'Science policy'                        43,360 --


# ######### plos journals 
# string_journal=""#   PLOS ONE"

# #list_strings=['PLOS MED', 'PLOS BIOL', 'PLOS COMPUT', 'PLOS PATHOG', 'PLO NE TR D', 'PLOS GENET', 'PLOS ONE']


# #for string_journal in list_strings:

#     # PLOS ONE       6,367,070
#     # PLOS GENET      149,923
#     # PLO NE TR D     138,289   # (neglected tropical diseases)
#     # PLOS PATHOG     109,803
#     # PLOS COMPUT      77,924
#     # PLOS BIOL        56,754
#     # PLOS MED         24,506



# #PLOS Medicine, PLOS Biol-ogy, PLOS Computational Biology, PLOS Pathology, PLOS Neglected Tropical Diseases, PLOSGenetics, and PLOS ONE


# ######### WoS subject categories. 
# string_plos_field=""#['D CU BIOLOGY']"

# # ['D RO MULTIDISCIPLINARY SCIENCES']                                                                                                       4464540
# # ['D CU BIOLOGY']                                                                                                                          1055045
# # ['D RO MULTIDISCIPLINARY SCIENCES', 'D CU BIOLOGY']                                                                                        847485
# # ['D KM GENETICS & HEREDITY']                                                                                                               149923
# # ['D YU TROPICAL MEDICINE', 'D TI PARASITOLOGY']                                                                                            138289
# # ['D ZE VIROLOGY', 'D QU MICROBIOLOGY', 'D TI PARASITOLOGY']                                                                                109803
# # ['D CO BIOCHEMICAL RESEARCH METHODS', 'D MC MATHEMATICAL & COMPUTATIONAL BIOLOGY']                                                          77687
# # ['D CQ BIOCHEMISTRY & MOLECULAR BIOLOGY', 'D CU BIOLOGY']                                                                                   56754
# # ['D PY MEDICINE, GENERAL & INTERNAL']                                                                                                       24506
# # ['D CO BIOCHEMICAL RESEARCH METHODS', 'D MC MATHEMATICAL & COMPUTATIONAL BIOLOGY', 'D PO MATHEMATICS, INTERDISCIPLINARY APPLICATIONS']        237











# print ("original size:",df_merged.shape)








# ##### preselection by plos year
# print (years)
# preselection_df = df_merged[df_merged['plos_pub_year'].isin(years)]  
# print ("size of preselection1 (by plos years):",preselection_df.shape)





# #### i remove self-citations
# if (string_self_ref==0) or  ( string_self_ref == 1 ): 
#     preselection_df = preselection_df[preselection_df['self_citation']== string_self_ref ]  
#     if string_self_ref ==0:
#         string_self_ref = ", no self-cit"
#     elif string_self_ref ==1:
#         string_self_ref = ", only self-cit"





# ######### preselection by isolated or group references:
# if (string_isolated_ref==0) or  ( string_isolated_ref == 1 ): 
#     preselection_df0 = preselection_df[preselection_df['isolated_citation']== string_isolated_ref ]  

#     if string_isolated_ref ==0:
#         string_isolated_ref = ", group ref"
#     elif string_isolated_ref ==1:
#         string_isolated_ref = ", isolated ref"
# else:    
#     preselection_df0 = preselection_df   
#     print ("size of preselection1 (by isolated/group ref):",preselection_df0.shape, string_isolated_ref)








# ######### preselection by plos ONE subject category:
# if string_code_categ=="": 
#     preselection_df111 = preselection_df0
# else:    
#     if " " not in string_code_categ:  # to include one single category
#         preselection_df111 = preselection_df0[preselection_df0['categ_codes'].str.contains(string_code_categ)]        
#         string_code_categ = " "+dict_code_categ[string_code_categ]  

#     else:  # if multiple codes-categories
#         list_codes = string_code_categ.split(" ")
#         print (list_codes)

#         if len(list_codes) >= 2:              
#             preselection_df111 = preselection_df0[ preselection_df0['categ_codes'].str.contains('|'.join(list_codes)) ]  # to look for partial matches from a list of strings!!!!!


#         string_code_categ = "" 
#         for code in list_codes:
#             string_code_categ += "-"+dict_code_categ[code] 


#     print (" size of preselection (by plos ONE subject category):",preselection_df111.shape, string_code_categ)








# ######### preselection by plos journal:
# if string_journal=="": 
#     preselection_df1 = preselection_df111
# else:    
#     preselection_df1 = preselection_df111[preselection_df111['plos_j1']== string_journal ]  
# print (" size of preselection2 (by plos journal):",preselection_df1.shape, string_journal)







# ######### preselection by plos field:
# if string_plos_field=="": 
#     preselection_df2 = preselection_df1
# else:    
#     preselection_df2 = preselection_df1[preselection_df1['plos_field']== string_plos_field ]  
# print (" size of preselection2 (by plos field):",preselection_df2.shape, string_plos_field)




# preselection_df3 = preselection_df2


# N_plos=len(preselection_df3.paper_UT.unique())        ## this values are overall, for the title   
# N_all=len(preselection_df3)



# fig_font_colors=''



# if v1_string ==  'cite_count'  or       v1_string ==  'log_num_cit_ref'   or v1_string == 'log2_num_cit_ref':



#     string_age_selection=''

#     ##### preselection only young/old references:        
#     if string_references_age == "young":
#         time_window = 1
#         string_age_selection="only young references from >="+ str((min(years)-time_window))
#         preselection_df3 = preselection_df2[preselection_df2['ref_pub_year'] >= (min(years)-time_window) ]   
#         print ("  size of preselection3 (only young references):",preselection_df3.shape, string_age_selection)

#     elif string_references_age == "old":
#         time_window = 10
#         string_age_selection="only old references from <="+str((min(years)-time_window))
#         preselection_df3 = preselection_df2[preselection_df2['ref_pub_year'] <= (min(years)-time_window) ]   
#         print ("  size of preselection3 (only young references):",preselection_df3.shape,string_age_selection )

#     else:
#         string_age_selection="young&old"       
#         print ("  No preselection by age of references:",preselection_df3.shape )




#     N_plos=len(preselection_df3.paper_UT.unique())        ## this values are overall, for the title   
#     N_all=len(preselection_df3)




#     #fig_colorscale = [[0, '#ffece6'], [1, '#ff0000']]   # if i give it a min and a max colors in HEX, it creates a gradient from one to another
    
    
# #     factor_color_rescale =.3   

# #     fig_colorscale=[[0.0*factor_color_rescale, '#ffffff'],\
# #                            [0.1*factor_color_rescale, '#d9f2d9'],\
# #                            [0.2*factor_color_rescale, '#c6ecc6'],\
# #                            [0.3*factor_color_rescale, '#b3e6b3'],\
# #                            [0.4*factor_color_rescale, '#8cd98c'], \
# #                            [0.5*factor_color_rescale, '#66cc66'], \
# #                            [0.6*factor_color_rescale, '#53c653'], \
# #                            [0.7*factor_color_rescale, '#40bf40'],\
# #                            [0.75*factor_color_rescale, '#39ac39'],\
# #                            [0.8*factor_color_rescale, '#339933'],\
# #                            [0.85*factor_color_rescale, '#2d862d'],\
# #                            [0.9*factor_color_rescale, '#267326'],\
# #                            [1.0, '#000000']]
   
    
    
    
# #     fig_font_colors = ['#ff0000', '#ffece6']      # same for the annotation of the boxes (to make sure they are readable)


#     fig_colorscale = "Reds"
#     fig_title_plot = "Median (final) number of citations of references in "+string_journal+string_plos_field+"<br> papers from "+str(years)+", "+string_age_selection+string_isolated_ref+string_self_ref+string_code_categ+"<br>Number of occurrences: "+str(N_all)#+",   Number plos: "+str(N_plos)
#     
  
# top_space = 150
# if v1_string ==  'cite_count'  :
#     colorbar_string = 'Citations'
#     if string_references_age == "old" :
#         colorbar_string = ''
# else:
#     colorbar_string = 'Age [yr]'
#     top_space = 100
#     text_abc = '(b)'fig_filename =   '../plots/annotated-heatmap_median_citations_of_references_for_sections_and_fract_subsection_by_citations_of_plos'

#     if  v1_string ==  'log_num_cit_ref' :
#         fig_title_plot = "Median log10 of (final) number of citations of references in "+string_journal+string_plos_field+"<br> papers from "+str(years)+", "+string_age_selection+string_isolated_ref+string_self_ref+string_code_categ+"<br>Number of occurrences: "+str(N_all)#+",   Number plos: "+str(N_plos)
#     elif  v1_string ==  'log2_num_cit_ref' :
#         fig_title_plot = "Median log2 of (final) number of citations of references in "+string_journal+string_plos_field+"<br> papers from "+str(years)+", "+string_age_selection+string_isolated_ref+string_self_ref+string_code_categ+"<br>Number of occurrences: "+str(N_all)#+",   Number plos: "+str(N_plos)







# elif v1_string =='ref_pub_year':
#     fig_colorscale = "Viridis"
#     fig_title_plot = "Median age of references in "+string_journal+string_plos_field+"<br> papers from "+str(years)+string_isolated_ref+string_self_ref+string_code_categ+"<br>Number of occurrences: "+str(N_all)#+",   Number plos: "+str(N_plos)
#     fig_filename = '../plots/annotated-heatmap_median_age_of_references_for_sections_and_fract_subsection_by_citations_of_plos'   
#     print ("  No preselection by age of references:",preselection_df3.shape )







# elif v1_string =='diff_year_plos_ref':

#     factor_color_rescale =.6  

#     fig_colorscale=[[0.0*factor_color_rescale, '#ffffff'],\
#                            [0.1*factor_color_rescale, '#d9f2d9'],\
#                            [0.2*factor_color_rescale, '#c6ecc6'],\
#                            [0.3*factor_color_rescale, '#b3e6b3'],\
#                            [0.4*factor_color_rescale, '#8cd98c'], \
#                            [0.5*factor_color_rescale, '#66cc66'], \
#                            [0.6*factor_color_rescale, '#53c653'], \
#                            [0.7*factor_color_rescale, '#40bf40'],\
#                            [0.75*factor_color_rescale, '#39ac39'],\
#                            [0.8*factor_color_rescale, '#339933'],\
#                            [0.85*factor_color_rescale, '#2d862d'],\
#                            [0.9*factor_color_rescale, '#267326'],\
#                           [1.0, '#000000']]
    
  
    
    
#     #fig_colorscale = [[0, 'dcf0d2'], [1, '205803']]   # if i give it a min and a max colors in HEX, it creates a gradient from one to another
#     fig_font_colors = ['#205803', '#dcf0d2']      # same for the annotation of the boxes (to make sure they are readable)
#     fig_title_plot = "Median difference between publication year of plos and references in "+string_journal+string_plos_field+" papers from "+str(years)+string_isolated_ref+string_self_ref+string_code_categ+"<br>Number of occurrences: "+str(N_all)#+",   Number plos: "+str(N_plos)
#     fig_filename = '../plots/annotated-heatmap_median_age_difference_plos_publ_year_vs_references_for_sections_and_subsect_by_citations_of_plos'

#     print ("  No preselection by age of references:",preselection_df3.shape )






# print ("\nTot # records included:",len(preselection_df3),"   # number of plos papers:",len(preselection_df3.paper_UT.unique()), "   # unique ref:", len(preselection_df3.reference_UT.unique()),'\n')


# print (preselection_df3.shape, "  <avg # cit ref>:",preselection_df3.cite_count.median())





# #### i get the bins number of citation of the plos papers OJO!!!!! i want the same bins for all papers (so i calculate them before separating into sections but after all the preselections)

# #quantiles=sorted(list(df_plos[string_filtering_x].quantile(list_q).to_dict().items())) #mean 10.68 
# quantiles=sorted(list(preselection_df3[string_filtering_x].quantile(list_q).to_dict().items())) #mean 10.68 


# lista_bins_plos_citations=[]
# old_value=0
# for item in quantiles:
#     try:
#         pair=[old_value, int(item[1])]    
#     except:  # if it is a nan:
#         pair=[old_value, item[1]]

#     lista_bins_plos_citations.append(pair)

#     try:
#         old_value = int(item[1])
#     except:
#         old_value = item[1]

# print (lista_bins_plos_citations)



# ### i modify the bins to separete the zero-one
# # lista_bins_plos_citations[0][0]=2       
# # lista_bins_plos_citations = [[0,2]] + lista_bins_plos_citations    
# #print (lista_bins_plos_citations)

# ################################################









# lista_titulos_sets = []



# lista_sections = ["Introduction","Methods","Results","Discussion"]

# cont=0
# for item in lista_bins_plos_citations:

#     minimo = item[0]
#     maximo = item[1]


#     preselection_df4 = preselection_df3[(preselection_df3[string_filtering_x] >= minimo)  &  (preselection_df3[string_filtering_x] < maximo)]
#     #print ("size of preselection3 (by cit bin plos):",df_select.shape, item)



#     x1_All = list(preselection_df4[v1_string])









#     for string_section in lista_sections:


#         ##### preselection to include only occurences in a section of the paper
#         if  string_section == "Introduction":
#             section=0
#         elif  string_section == "Methods":
#             section=1
#         elif  string_section == "Results":
#             section=2
#         elif  string_section == "Discussion":
#             section=3





#         df_select = preselection_df4[preselection_df4['regex_sect_index']== section]   
#         #print ("size of preselection2 (by section):",preselection_df3.shape, string_section)

#         x1 = list(df_select[v1_string])       





#         if cont ==0:            
#             #group=string_section+" Bottom "+str(int(100.*list_q[0]))+"%"  
#             group=string_section+" Bottom" 
#         elif cont ==1:            
#             #group=string_section+" "+str(int(100.*list_q[0]+1))+"%-"+str(int(100.*list_q[-4]))+"%"         
#             group=string_section+" Typical"       
#         elif cont==2:
#              #group=string_section+" "+str(int(100.*list_q[1]+1))+"%-"+str(int(100.*list_q[-3]))+"%"     
#              group=string_section+" Good"    
#         elif cont==3: 
#             #group=string_section+" "+str(int(100.*list_q[2]+1))+"%-"+str(int(100.*list_q[-2]))+"%"    
#             group=string_section+" High"
#         elif cont==4:
#             #group=string_section+" Top "+str(int(100.-100.*list_q[-2]))+"%"    
#             group=string_section+" Top"
            
            
#         lista_titulos_sets.append(group)    





#         ######### i get also quantiles for each cell:    
#         list_quantiles_cell=[.25,.5,.75]

#         values_quantiles=list(df_select[v1_string].quantile(list_quantiles_cell))#sorted(list(df_select[v1_string].quantile(list_quantiles_cell).to_dict().items()))      

#         tupla=values_quantiles + [len(x1)]

#         dict_group_quantiles_size[group] = tupla

#         dict_group_subset_data[group]=x1



#     cont +=1





# ################ i also add the median values for the section across all data in the preselection
# for string_section in lista_sections:


#     if  string_section == "Introduction":
#         section=0
#     elif  string_section == "Methods":
#         section=1
#     elif  string_section == "Results":
#         section=2
#     elif  string_section == "Discussion":
#         section=3


#     df_select = preselection_df3[preselection_df3['regex_sect_index']== section]   

#     list_quantiles_cell=[.25,.5,.75]
#     values_quantiles=list(df_select[v1_string].quantile(list_quantiles_cell))#sorted(list(df_select[v1_string].quantile(list_quantiles_cell).to_dict().items()))      
#     tupla=values_quantiles + [len(df_select)]



# #     dict_group_quantiles_size[string_section+" ALL PLOS"]=tupla
# #     dict_group_subset_data[string_section+" ALL PLOS"]=x1_All    







# ########  I create the x, y, z lists of values for the heatmap

# lista_y=lista_sections
# #lista_x=[" Bottom 30%"," 31% to 60%"," 61% to 90%" ," 91% to 99%"," Top 1%"," ALL"]
# #lista_bin_names=[" ALL PLOS"," Bottom "+str(int(100.*list_q[0]))+"%"," "+str(int(100.*list_q[0]+1))+"% to "+str(int(100.*list_q[-4]))+"%",\
#               #   " "+str(int(100.*list_q[1]+1))+"% to "+str(int(100.*list_q[-3]))+"%" ," "+str(int(100.*list_q[2]+1))+"% to "+str(int(100.*list_q[-2]))+"%"," Top "+str(int(100.-100.*list_q[-2]))+"%"]


# lista_bin_names=[" Bottom"," Typical"," Good"," High"," Top"]






# #lista_x=[" Bottom 30%"," 31% to 60%"," 61% to 90%" ," 91% to 99%"," Top 1%"]   

# lista_x=lista_bin_names

# lista_z25=[]
# lista_z50=[]
# lista_z75=[]
# lista_z_sizes=[]

# for x_value in lista_x:    
#     aux_lista25=[]
#     aux_lista50=[]
#     aux_lista75=[]
#     aux_lista_sizes=[]

#     for y_value in lista_y:       

#         llave=y_value+x_value

#         try:
#             value=int(dict_group_quantiles_size[llave][0])
#         except:  # if it is a nan:
#             value=dict_group_quantiles_size[llave][0]
#         aux_lista25.append(value)




#         try:
#             value=int(dict_group_quantiles_size[llave][1])
#         except:  # if it is a nan:
#             value=dict_group_quantiles_size[llave][1]
#         aux_lista50.append(value)




#         try:
#             value=int(dict_group_quantiles_size[llave][2])
#         except:  # if it is a nan:
#             value=dict_group_quantiles_size[llave][2]
#         aux_lista75.append(value)




#         value_size=dict_group_quantiles_size[llave][3]
#         aux_lista_sizes.append(value_size)


#         #print (y_value," ",x_value, value, value_size)
#     lista_z25.append(aux_lista25)
#     lista_z50.append(aux_lista50)
#     lista_z75.append(aux_lista75)




#     lista_z_sizes.append(aux_lista_sizes)



# # print ("lista values 25%-quantile:",lista_z25)
# # print ("lista sizes",lista_z_sizes)





# lista_text_z=[]
# for i in range(len(lista_z_sizes)):
#     aux=[]
#     for j in range(len(lista_z_sizes[0])):
#         #value=str(lista_z25[i][j])+"-<b>"+str(lista_z50[i][j])+"</b>-"+str(lista_z75[i][j])+"<br>("+str(lista_z_sizes[i][j])+")"            #"Median:"+str(lista_z[i][j])+"<br> N:"+str(lista_z_sizes[i][j])
#         value=str(lista_z25[i][j])+"-<b>"+str(lista_z50[i][j])+"</b>-"+str(lista_z75[i][j])+"<br>("+str(format(lista_z_sizes[i][j], ',d'))+")"            #"Median:"+str(lista_z[i][j])+"<br> N:"+str(lista_z_sizes[i][j])



#         aux.append(value)
#     lista_text_z.append(aux)
# # print (lista_text_z)





# ##### using a different library
# path=   '/home/staff/julia/at_Northwestern/In_Text_Citations/In-Text-Citations-New/plots/'


# fig = ff.create_annotated_heatmap(z=lista_z50, x=lista_sections, y=lista_bin_names, annotation_text=lista_text_z, colorscale=fig_colorscale, font_colors=fig_font_colors,showscale=True, colorbar=dict(title=colorbar_string, titleside='right' ),)#, reversescale=True)

# #fig = ff.create_annotated_heatmap(z=lista_z50, x=lista_sections, y=lista_bin_names,  colorscale=fig_colorscale, font_colors=fig_font_colors,showscale=True)#, reversescale=True)
# fig.layout.title = ""# fig_title_plot

# fig['layout']['xaxis']['side'] = 'bottom'
# fig.layout.xaxis.update({'title': 'Section'})


# fig.layout.yaxis.update({'title': 'Impact Group'})
# if v1_string ==  'cite_count'  :
#     if string_references_age == "young":  
#         fig.layout.yaxis.update({'title': ''})




# font_gral=25  # 20 if i wanna see it on the browser, 40 if i care about the png output
# fig['layout']['font']['size'] = font_gral

      
# if v1_string ==  'cite_count'  :
#     if string_references_age == "young":  
#         #fig.layout.update({'title': '$d, r \\text{ (solar radius)}$'})
#         fig['layout']['title'] = "Young references"
#     elif string_references_age == "old":  
#         fig.layout.update({'title': 'Old references'})

#     fig.layout.update({'font': dict(size=25)})

# # fig.layout.yaxis.update({'title': 'Citation percentile of plos paper'})




# font_gral=55  # 20 if i wanna see it on the browser, 40 if i care about the png output
# fig['layout']['font']['size'] = font_gral


# # Altering x axis
# #fig['layout']['xaxis']['tickfont']['family'] = 'Gill Sans MT'
# fig['layout']['xaxis']['tickangle'] = 0
# fig['layout']['yaxis']['tickangle'] = -90
# fig['layout']['xaxis']['titlefont']['size'] = font_gral + 20
# fig['layout']['yaxis']['titlefont']['size'] = font_gral

# fig['layout']['xaxis']['tickfont']['size'] = font_gral -7 
# fig['layout']['yaxis']['tickfont']['size'] = font_gral -15




# fig['layout']['margin']=dict(
#         l=200,
#        # r=50,
#         b=150,
#         t=top_space,
#         pad=15
#     )





# #  annotations=[
# #         dict(
# #             x=-.05,
# #             y=1.05,
# #             xref='paper',
# #             yref='paper',
# #             text=text_abc,
# #             showarrow=False,
# #             font=dict(               
# #                 size=80,  
# #                 color='black'
# #             ),
           
# #         )
# #     ],


# offline.plot(fig, auto_open=True, image = 'png', image_filename=fig_filename ,image_width=2000, image_height=1200, filename=fig_filename+'.html', validate=True)





# # old, age >=15 years; Tot # records included: 88209    # number of plos papers: 12895    # unique ref: 61867 
# # young, age <=2 years;  Tot # records included: 104113    # number of plos papers: 13442    # unique ref: 66644 












# ###########################################
# ######################################################3
# ########################################################


# ##############  I RUN THE TESTS FOR THE COMPARISON OF ALL PAIRS OF SUB-SETS:  (all pair-wise comparison cells in figure 2b, and 3a, 2b)

# #####  mann-whitney U   test



# lista_indeces = [[1,1],[1,2],[1,3],[1,4],\
#                  [2,1],[2,2],[2,3],[2,4],\
#                  [3,1],[3,2],[3,3],[3,4],\
#                  [4,1],[4,2],[4,3],[4,4],\
#                  [5,1],[5,2],[5,3],[5,4]]

# #fig_colorscale=  [ [0., '#f2f2f2'], [threshold_zero,'#cce6ff'], [0.9999, '#0059b3'], [1.,'#bdbdbd']]# '#ffffff']]  0: white,  .99999: blue,  1: grey
# fig_colorscale=  [ [0., '#0059b3'], [.5,'#c7dcf1'], [1.,'#bdbdbd']] #  0 or anything significant: blue,   .5 or anithing NON signif: light-blue,     1: grey






# lista_bin_names = ["Bottom","Typical","Good","High","Top"]
# lista_sections  =  ['Intro', 'Methods', 'Results', 'Discussion']






# tot_rows = 5
# tot_cols = 4  
    
# test = "MW"  # KS to test if the distributions are different or  MW for testing just whether the medians are different 
    

    
    
# list_keys_macro = ['Introduction Top',    'Methods Top',    'Results Top',   'Discussion Top', \
#                    'Introduction High',   'Methods High',  'Results High',  'Discussion High', \
#                    'Introduction Good',   'Methods Good',   'Results Good',  'Discussion Good', \
#                    'Introduction Typical', 'Methods Typical', 'Results Typical', 'Discussion Typical', \
#                    'Introduction Bottom',  'Methods Bottom',  'Results Bottom', 'Discussion Bottom']
    
      
# list_keys_heatmap = ['Introduction Bottom', 'Methods Bottom',  'Results Bottom', 'Discussion Bottom',\
#                      'Introduction Typical', 'Methods Typical', 'Results Typical', 'Discussion Typical',\
#                      'Introduction Good',   'Methods Good',   'Results Good',  'Discussion Good', \
#                      'Introduction High',   'Methods High',  'Results High',  'Discussion High', \
#                      'Introduction Top',   'Methods Top',    'Results Top',   'Discussion Top'  ]


# ### i apply the bonferroni correction:  new p-_value_threshold  required for significance = old_p_value /Number of comparisons = 0.001 / (20*19/2)     
    
# threshold_zero = 0.0001 / (float(len(list_keys_macro))*float(len(list_keys_macro)-1)/2.)    # to round up to zero the very small p_values



# # lista_titulos_sets  (from the previous cell)

# # ['Introduction Bottom',
# #  'Methods Bottom',
# #  'Results Bottom',
# #  'Discussion Bottom',
# #  'Introduction Typical',
# #  'Methods Typical',
# #  'Results Typical',
# #  'Discussion Typical',
# #  'Introduction Good',
# #  'Methods Good',
# #  'Results Good',
# #  'Discussion Good',
# #  'Introduction High',
# #  'Methods High',
# #  'Results High',
# #  'Discussion High',
# #  'Introduction Top',
# #  'Methods Top',
# #  'Results Top',
# #  'Discussion Top']






# lista_tot_datos=[]

# total_cont =0
# for i in list_keys_macro:
#     lista_listas=[]
#     aux_lista=[]
#     cont=1
   
#     for j in list_keys_heatmap:
             
#         set1 = dict_group_subset_data[i]
#         set2 = dict_group_subset_data[j]
        
#         if test == "KS":
#             p_value = stats.ks_2samp(set1, set2)[1] 
#         elif test == "MW":
#             p_value = stats.mannwhitneyu(set1, set2,  alternative='two-sided')[1]  
        
        
#         if p_value <= threshold_zero:  #i round up to zero the very small p_values
#                 p_value =0.
                
#         else:
#             p_value = .5  ### I ONLY CARFE ABOUT WHETGER IT IS SIGNIFICANT OR NOT, I DONT CARE ABOUT THE EXACT P-VALUE ONCE IT IS NOT SIGNIFICANT
                
#         if i == j:  # i single out manually the self comparison
#             p_value=1.001  
            
            
            
#         aux_lista.append(p_value)
        
#         cont +=1
        
#         if cont > tot_cols:
#             lista_listas.append(aux_lista)                  
#             aux_lista=[]
#             cont=1
            
    
    
#     total_cont +=1
#     lista_tot_datos.append(lista_listas)
    
    
   


# ##############################

# ### I create an empty plot
# fig_macro = None
# fig_macro = tools.make_subplots(rows=tot_rows, cols=tot_cols, shared_xaxes=True, shared_yaxes=True, vertical_spacing = 0.01, horizontal_spacing = 0.01,   )


# for i in range(len(lista_tot_datos)):
#     datos = lista_tot_datos[i]
    
#     cont_rows = lista_indeces[i][0]
#     cont_cols = lista_indeces[i][1]
    
#     trace1 = go.Heatmap(z=datos,
#                        x=lista_sections,
#                        y=lista_bin_names,                        
#                        colorscale = fig_colorscale,
#                        showscale=False,)
#                         #reversescale=True, )#    )

   



    
#     # i add each plot
#     fig_macro.append_trace(trace1, cont_rows, cont_cols)


 



# fontsize=32 
# fig_macro['layout']['font'].update({'size': fontsize})






# # fig_macro['layout']['margin'].update({'l': 250})   # i add extra space to the margins of the plots
# # fig_macro['layout']['margin'].update({'b': 150})  
# # fig_macro['layout']['margin'].update({'t': 50})   



# lista_bin_names = ["Bottom","Typical","Good","High","Top"]
# lista_sections  =  ['Introduction', 'Methods', 'Results', 'Discussion']



# # i use the axis title of the small plots as values of the axis of the macro plot
# fig_macro['layout']['xaxis1'].update(title=lista_sections[0])  
# fig_macro['layout']['xaxis2'].update(title=lista_sections[1])
# fig_macro['layout']['xaxis3'].update(title=lista_sections[2])
# fig_macro['layout']['xaxis4'].update(title=lista_sections[3])


# fig_macro['layout']['yaxis1'].update(title=lista_bin_names[4])   # ojo con el orden aqui!!
# fig_macro['layout']['yaxis2'].update(title=lista_bin_names[3])
# fig_macro['layout']['yaxis3'].update(title=lista_bin_names[2])
# fig_macro['layout']['yaxis4'].update(title=lista_bin_names[1])
# fig_macro['layout']['yaxis5'].update(title=lista_bin_names[0])







# #  annotations=[
# #         dict(
# #             x=-.05,
# #             y=1.05,
# #             xref='paper',
# #             yref='paper',
# #             text='(b)',
# #             showarrow=False,
# #             font=dict(               
# #                 size=80,  
# #                 color='black'
# #             ),
           
# #         )
# #     ],
   
         
         


    

# offline.plot(fig_macro, auto_open=True, image = 'png', image_filename='multiplot_comparisons' ,image_width=3000, image_height=2200,
#               filename='../plots/multiplot_comparisons.html', validate=True)






In [ ]:
# #####  i combine the reference records from two different fields for benchmarking:


# ########  FALTA!!! TAKE ONLY UNIQUE REFERENCES THAT BELONG ONLY TO ONE FIELD OR THE OTHER!!






# df_comput = pickle.load(open('../data/df_abstracts_titles_ref_2010comput.pkl', 'rb'))
# df_comput = df_social.sort_values(by=['reference_UT']).reset_index(drop=True)
# list_ref_comput = df_social.reference_UT.unique()




# df_social = pickle.load(open('../data/df_abstracts_titles_ref_2010social.pkl', 'rb'))
# df_social = df_social.sort_values(by=['reference_UT']).reset_index(drop=True)
# list_ref_social = df_social.reference_UT.unique()


# df_physical = pickle.load(open('../data/df_abstracts_titles_ref_2010physical.pkl', 'rb'))
# df_physical = df_physical.sort_values(by=['reference_UT']).reset_index(drop=True)
# list_ref_physical = df_physical.reference_UT.unique()

# df_biol = pickle.load(open('../data/df_abstracts_titles_ref_biol_2010.pkl', 'rb'))
# df_biol = df_biol.sort_values(by=['reference_UT']).reset_index(drop=True)
# list_ref_biol = df_biol.reference_UT.unique()


# len(set(list_ref_biol) & set(list_ref_physical))      #  bio 32347   & #  social 3474   #  physical  11197
# #len(set(list_ref_physical))   




# ###########################3


# two_categ_df = pd.concat([df_social,df_biol])


# print (two_categ_df.shape)
# two_categ_df  = two_categ_df.drop_duplicates(subset=['reference_UT'])


# print (two_categ_df.shape)

# two_categ_df = two_categ_df.sort_values(by=['reference_UT']).reset_index(drop=True)

# print (two_categ_df.shape)



# with open('../data/df_abstracts_titles_ref_SOCIAL_and_BIOL_2010.pkl', 'wb') as handle:
#             pickle.dump(two_categ_df, handle, protocol = 2)
        
# print ("written:",'../data/df_abstracts_titles_ref_SOCIAL_and_BIOL_2010.pkl',len(two_categ_df))   





# print (df_social.shape, df_biol.shape, df_physical.shape, two_categ_df.shape)


# two_categ_df
